In [1]:
# Imports / Configs / Global vars

# Import of native python tools
import os

# Visualization libraries
# import plotly.express as px

# Logging configuraiton
import logging
logging.basicConfig(format='[ %(asctime)s ][ %(levelname)s ]: %(message)s', datefmt='%m/%d/%Y %I:%M:%S %p')
logger = logging.getLogger()
logger.setLevel(logging.INFO)


# Ipython configs
from IPython.core.display import display, HTML
from IPython.core.interactiveshell import InteractiveShell
display(HTML("<style>.container { width:90% !important; }</style>"))
InteractiveShell.ast_node_interactivity = 'all'

# Pandas configs
import pandas as pd
pd.options.display.max_rows = 350
pd.options.display.max_columns = 250
import plotly.express as px
from plotly.offline import init_notebook_mode, iplot

init_notebook_mode(connected=True)

# Jupyter configs
%load_ext autoreload
%autoreload 2
%config Completer.use_jedi = False

/var/folders/0b/hbv1x9fd5f37yqz3mxj52y5r0000gq/T/ipykernel_13857/1337180755.py:17: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display, HTML


# Data

In [2]:
oil_price = pd.read_csv('../data/02_intermediate/oil_price.csv', parse_dates=['date'])
kase = pd.read_csv('../data/02_intermediate/securities.csv', parse_dates=['date'])
kase = kase[kase['type'] == 'акции'].reset_index(drop=True)
daily_curr_agg = pd.read_csv('../data/02_intermediate/currencies.csv', parse_dates=['date'])

In [3]:
daily_curr_agg

date         USD         EUR       RUB       KGS         GBP   
0   2022-09-01  472.958333  473.687500  7.441667  5.843750  568.333333  \
1   2022-09-02  473.200000  473.075000  7.441250  5.750000  556.500000   
2   2022-09-03  473.166667  473.000000  7.375000  5.725000  555.000000   
3   2022-09-04  472.000000  473.500000  7.375000  5.725000  555.000000   
4   2022-09-05  472.970588  472.264706  7.395588  5.689706  555.000000   
..         ...         ...         ...       ...       ...         ...   
507 2022-02-24  458.003409  512.844318  5.479659  5.357386  624.045455   
508 2022-02-25  466.634146  523.195122  5.664024  5.402439  640.000000   
509 2022-02-26  460.607143  518.857143  5.637143  5.400000  635.714286   
510 2022-02-27  464.708333  522.333333  5.617778  5.400000  637.222222   
511 2022-02-28  494.630435  455.239130  4.343478  4.539130  550.108696   

           CNY           GLD         CHF        HKD         GEL         AED   
0    67.000000  26195.833333  478.750000  56.000000  141.000000  121.083333  \
1    67.000000  25900.000000  475.000000  56.000000  141.000000  121.000000   
2    66.000000  25900.000000  475.000000  56.000000  141.000000  121.000000   
3    65.000000  25900.000000  475.000000  56.000000  141.000000  121.000000   
4    65.000000  25900.000000  475.000000  56.000000  141.000000  121.000000   
..         ...           ...         ...        ...         ...         ...   
507  69.573864  27763.920455  509.284091  54.289773  145.397727  116.130682   
508  71.000000  28897.560976  528.000000  59.000000  150.000000  122.500000   
509  71.000000  28800.000000  519.357143  59.000000  150.000000  122.500000   
510  71.277778  29366.666667  510.444444  59.000000  150.000000  122.500000   
511  61.782609  30482.608696  445.760870  59.000000  151.739130  126.086957   

          INR         CAD         MYR         PLN        THB        TRY   
0    5.400000  335.000000   96.000000  109.000000  12.700000  33.166667  \
1    5.400000  335.000000   96.000000  109.000000  12.700000  33.000000   
2    5.400000  335.000000   96.000000  109.000000  12.700000  33.000000   
3    5.400000  335.000000   96.000000  109.000000  12.700000  33.000000   
4    5.400000  335.000000   96.000000  109.000000  12.700000  33.000000   
..        ...         ...         ...         ...        ...        ...   
507  5.803977  347.897727   99.647727  109.397727  13.585227  37.568182   
508  6.600000  357.500000  107.000000  114.000000  14.750000  36.000000   
509  6.600000  357.500000  107.000000  114.000000  14.750000  36.000000   
510  6.600000  357.500000  107.000000  114.000000  14.750000  36.000000   
511  6.626087  368.858696  108.130435  115.173913  15.027174  38.500000   

          UZS        UAH        CZK         ILS        KRW       JPY  
0    4.050000  16.700000  18.425000  125.000000  37.000000  3.300000  
1    4.050000  16.700000  18.500000  125.000000  37.000000  3.300000  
2    4.050000  16.700000  18.500000  125.000000  37.000000  3.300000  
3    4.050000  16.700000  18.500000  125.000000  37.000000  3.300000  
4    4.050000  16.700000  18.500000  125.000000  37.000000  3.300000  
..        ...        ...        ...         ...        ...       ...  
507  4.031818  16.672727  19.467045  132.159091  36.818182  3.600000  
508  4.050000  16.300000  20.600000  142.500000  36.000000  3.600000  
509  4.050000  16.300000  20.600000  142.500000  36.000000  3.600000  
510  4.050000  16.300000  20.600000  142.500000  36.000000  3.600000  
511  4.102174  16.300000  20.767391  144.782609  36.913043  3.665217  

[512 rows x 24 columns]

In [4]:
kase = kase.sort_values(by=['ticker', 'date']).reset_index(drop=True)

### Target value anomaly detection

In [5]:
# Anomaly filration
import plotly.express as px


fig = px.line(
    kase,
    x="date", y="calculated_cost", color="ticker",
    template='plotly_dark',
    title='Stocks price changes over time period for different companies')
# fig.show()

In [6]:
fig.show()

From the news seen that tesla & amazon has been experienced stock split
We need to filter out data before splitting

In [7]:
kase = kase[~((kase['ticker'] == 'AMZN_KZ') & (kase['date'] < pd.to_datetime('2022-06-07')))].reset_index(drop=True)
kase = kase[~((kase['ticker'] == 'TSLA_KZ') & (kase['date'] < pd.to_datetime('2022-08-26')))].reset_index(drop=True)

In [8]:
# Anomaly filration
import plotly.express as px


fig = px.line(
    kase,
    x="date", y="calculated_cost", color="ticker",
    template='plotly_dark',
    title='Stocks price changes over time period for different companies')
fig.show()

In [9]:
oil_price_melted = pd.melt(
    oil_price,
    id_vars=['date']
)
oil_price_melted = oil_price_melted.sort_values(by=['date']).reset_index(drop=True).rename(columns={'variable': 'price', 'value': '$(USD)/BARREL'})
prices_cols = ['price_per_barrel', 'price_per_barrel_min', 'price_per_barrel_max']
volume_col = ['price_per_barrel_volume']
lag_col = ['relative_diff_lag_1']
oil_price_melted.head()

date                    price  $(USD)/BARREL
0 2021-12-01     price_per_barrel_max          72.87
1 2021-12-01  price_per_barrel_volume         420.40
2 2021-12-01     price_per_barrel_min          68.14
3 2021-12-01    price_per_barrel_open          69.80
4 2021-12-01         price_per_barrel          68.87

In [10]:

fig = px.line(
    oil_price_melted[oil_price_melted['price'].isin(prices_cols)],
    x="date", y="$(USD)/BARREL", color="price",
    template='plotly_dark',
    title='Oil (avg, min & max prices)')
fig.show()

In [11]:
fig = px.line(
    oil_price_melted[oil_price_melted['price'].isin(volume_col)],
    x="date", y="$(USD)/BARREL", color="price",
    template='plotly_dark',
    title='Oil volume price: ')
fig.show()

In [12]:
daily_curr_agg_melted = pd.melt(daily_curr_agg, id_vars=['date']).rename(columns={'variable': 'currency', 'value': 'price'})
daily_curr_agg_melted = daily_curr_agg_melted.sort_values(by=['currency', 'date']).reset_index(drop=True)

fig = px.line(
    daily_curr_agg_melted,
    x="date", y="price", color="currency",
    template='plotly_dark',
    title='Currency price: ')
fig.show()

In [13]:
daily_curr_agg_melted = daily_curr_agg_melted[daily_curr_agg_melted['currency'] != 'GLD']

In [14]:
fig = px.line(
    daily_curr_agg_melted,
    x="date", y="price", color="currency",
    template='plotly_dark',
    title='Currency price: ')
fig.show()

### Euro has anomaly value at 2022.05.18

In [15]:
daily_curr_agg_melted = daily_curr_agg_melted[daily_curr_agg_melted['price'] < 2000].reset_index(drop=True)

In [16]:
fig = px.line(
    daily_curr_agg_melted,
    x="date", y="price", color="currency",
    template='plotly_dark',
    title='Currency price: ')
fig.show()

### Anomalic jump of  USD  at 2022.06.11

In [17]:
# daily_curr_agg_melted = daily_curr_agg_melted[daily_curr_agg_melted['price'] < 2000].reset_index(drop=True)
daily_curr_agg_melted = daily_curr_agg_melted[~((daily_curr_agg_melted['currency'] == 'USD') & (daily_curr_agg_melted['date'] == pd.to_datetime('2022-06-11')))].reset_index(drop=True)

In [18]:
# Revert back melted table
daily_curr_agg = daily_curr_agg_melted.pivot_table(
    values='price',
    columns='currency',
    index='date',
).reset_index()
daily_curr_agg

currency       date    AED    CAD         CHF        CNY   CZK         EUR   
0        2021-12-01  115.0  345.0  482.000000  67.900000  18.9  499.600000  \
1        2021-12-02  115.0  345.0  481.571429  67.900000  18.9  499.142857   
2        2021-12-03  115.0  345.0  481.000000  67.900000  18.9  497.500000   
3        2021-12-04  115.0  345.0  481.000000  67.900000  18.9  496.500000   
4        2021-12-06  115.0  345.0  481.000000  67.900000  18.9  496.285714   
..              ...    ...    ...         ...        ...   ...         ...   
490      2023-05-01  117.0  330.0  500.000000  68.500000  21.0  498.500000   
491      2023-05-02  117.0  330.0  497.826087  68.500000  21.0  496.130435   
492      2023-05-03  117.0  330.0  491.627907  68.633721  21.0  492.517442   
493      2023-05-04  117.0  330.0  490.000000  68.722222  21.0  494.250000   
494      2023-05-05  117.0  330.0  490.000000  69.000000  21.0  493.535714   

currency         GBP    GEL   HKD    ILS  INR  JPY       KGS   KRW   MYR   
0         588.000000  141.0  53.0  125.0  5.4  3.6  5.050000  37.5  96.0  \
1         586.285714  141.0  53.0  125.0  5.4  3.6  5.050000  37.5  96.0   
2         585.000000  141.0  53.0  125.0  5.4  3.6  5.050000  37.5  96.0   
3         585.000000  141.0  53.0  125.0  5.4  3.6  5.050000  37.5  96.0   
4         585.285714  141.0  53.0  125.0  5.4  3.6  5.050000  37.5  96.0   
..               ...    ...   ...    ...  ...  ...       ...   ...   ...   
490       580.000000  162.5  56.0  116.0  5.0  3.6  5.250000  34.0  99.0   
491       577.608696  162.5  56.0  116.0  5.0  3.6  5.250000  34.0  99.0   
492       571.511628  162.5  56.0  116.0  5.0  3.6  5.250000  34.0  99.0   
493       570.000000  162.5  56.0  116.0  5.0  3.6  5.250000  34.0  99.0   
494       570.000000  162.5  56.0  116.0  5.0  3.6  5.294643  34.0  99.0   

currency    PLN       RUB   THB   TRY   UAH         USD   UZS  
0         109.0  5.870000  12.7  39.0  16.7  436.400000  4.05  
1         109.0  5.881429  12.7  39.0  16.7  437.392857  4.05  
2         109.0  5.939000  12.7  39.0  16.7  438.175000  4.05  
3         109.0  5.960000  12.7  39.0  16.7  438.500000  4.05  
4         109.0  5.945714  12.7  39.0  16.7  438.750000  4.05  
..          ...       ...   ...   ...   ...         ...   ...  
490       110.0  5.500000  15.0  25.5   8.5  452.750000  4.50  
491       110.0  5.500000  15.0  25.5   8.5  450.706522  4.50  
492       110.0  5.524419  15.0  25.5   8.5  445.872093  4.50  
493       110.0  5.568056  15.0  25.5   8.5  446.152778  4.50  
494       110.0  5.728571  15.0  25.5   8.5  446.089286  4.50  

[495 rows x 23 columns]

In [19]:
daily_curr_agg.isna().sum()

currency
date    0
AED     0
CAD     0
CHF     0
CNY     0
CZK     0
EUR     1
GBP     0
GEL     0
HKD     0
ILS     0
INR     0
JPY     0
KGS     0
KRW     0
MYR     0
PLN     0
RUB     0
THB     0
TRY     0
UAH     0
USD     1
UZS     0
dtype: int64

## Building a dataset
Okay, we've filtered anomalies:
- anomaly currency prices for USD & EUR
- stocks splits for Amazon & Tesla


In [20]:
base_dataset = kase \
    .merge(
        daily_curr_agg,
        how='left'
    ) \
    .merge(
        oil_price,
        how='left'
    )


In [21]:
base_dataset.to_csv('../data/03_primary/dataset.csv', index=False)

In [22]:
# Aggregation of lag data
import datetime


def generate_date_range(date: datetime.datetime, last_n_days: int):
    
    date_range = pd.date_range(
        start=date - datetime.timedelta(days=last_n_days),
        end=date,
    )
    return date_range


def select_df_in_daterange(df: pd.DataFrame, date_range: list[datetime.datetime]):
    return df[df['date'].isin(date_range)]

def agg_last_days(df: pd.DataFrame, date: datetime.datetime, last_n_days: int):
#     metrics = ['max', 'min', 'median']
    metrics = df.drop(columns=['date'], errors='ignore')
    
    median = metrics.median()
    median.index = 'median('+ pd.Series(median.index) + f')_last_{last_n_days}_days'
    
    max_agg = metrics.max()
    max_agg.index = 'max('+ pd.Series(max_agg.index) + f')_last_{last_n_days}_days'
    
    min_agg = metrics.min()
    min_agg.index = 'max('+ pd.Series(min_agg.index) + f')_last_{last_n_days}_days'
    
    df = pd.DataFrame(pd.concat([min_agg, median, max_agg], axis=0)).T
    df['date'] = date
    return df


def agg_last_lags(curr: pd.DataFrame, last_n_days):
    lag_days_metrics = []
    for agg_date in curr['date'].unique():
        agg_date_range = generate_date_range(agg_date, last_n_days=last_n_days)

        selected_df = select_df_in_daterange(
            df=curr,
            date_range=agg_date_range,
        )

        lag = agg_last_days(
            selected_df,
            date=agg_date,
            last_n_days=last_n_days,
        )
        logging.info(f'Finish: {agg_date}')
        lag_days_metrics.append(lag)

    return pd.concat(lag_days_metrics).reset_index(drop=True)


In [23]:
curr_lag_7_days = agg_last_lags(daily_curr_agg.copy(), last_n_days=7)
curr_lag_30_days = agg_last_lags(daily_curr_agg.copy(), last_n_days=30)
oil_lag_7 = agg_last_lags(oil_price, last_n_days=7)
oil_lag_30 = agg_last_lags(oil_price, last_n_days=30)

[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-01 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-02 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-03 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-04 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-06 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-07 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-08 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-09 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-10 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-11 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-12 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-13 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-14 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-15 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2021-12-16 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Fini

[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-02 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-03 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-04 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-05 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-06 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-07 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-08 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-09 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-10 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-11 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-12 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-13 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-14 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-15 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Finish: 2022-05-16 00:00:00
[ 05/06/2023 09:26:07 PM ][ INFO ]: Fini

[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-10 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-11 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-12 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-13 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-14 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-15 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-16 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-17 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-18 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-19 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-20 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-21 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-22 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-23 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-09-24 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Fini

[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-18 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-19 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-20 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-21 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-22 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-23 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-24 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-25 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-26 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-27 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-28 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-29 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-30 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-01-31 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2023-02-01 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Fini

[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2021-12-23 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2021-12-24 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2021-12-25 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2021-12-26 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2021-12-27 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2021-12-28 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2021-12-29 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2021-12-30 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2021-12-31 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-01-03 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-01-17 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-01-18 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-01-19 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-01-20 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Finish: 2022-01-21 00:00:00
[ 05/06/2023 09:26:08 PM ][ INFO ]: Fini

...

[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-09-05 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-09-02 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-09-01 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-31 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-30 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-29 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-26 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-25 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-24 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-23 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-22 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-19 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-18 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-17 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Finish: 2022-08-16 00:00:00
[ 05/06/2023 09:26:09 PM ][ INFO ]: Fini

[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-03-07 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-03-04 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-03-03 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-03-02 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-03-01 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-28 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-25 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-24 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-23 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-22 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-21 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-18 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-17 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-16 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-15 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Fini

[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-02-09 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-02-08 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-02-07 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-02-06 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-02-03 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-02-02 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-02-01 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-01-31 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-01-30 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-01-27 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-01-26 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-01-25 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-01-24 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-01-23 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2023-01-20 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Fini

[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-08-10 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-08-09 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-08-08 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-08-05 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-08-04 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-08-03 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-08-02 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-08-01 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-07-29 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-07-28 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-07-27 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-07-26 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-07-25 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-07-22 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-07-21 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Fini

[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-09 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-08 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-07 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-04 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-03 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-02 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-02-01 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-01-31 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-01-28 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-01-27 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-01-26 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-01-25 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-01-24 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-01-21 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Finish: 2022-01-20 00:00:00
[ 05/06/2023 09:26:10 PM ][ INFO ]: Fini

In [24]:
lag_aggregated = kase \
    .merge(
        daily_curr_agg,
        how='left'
    ) \
    .merge(
        curr_lag_7_days,
        how='left'
    ) \
    .merge(
        curr_lag_30_days,
        how='left'
    ) \
    .merge(
        oil_price,
        how='left'
    ) \
    .merge(
        oil_lag_7,
        how='left'
    ) \
    .merge(
        oil_lag_30,
        how='left'
    )

In [28]:
lag_aggregated.to_csv('../data/03_primary/dataset_with_lag_aggregates.csv', index=False)